In [1]:
import sklearn.neighbors._base
import sys
sys.modules['sklearn.neighbors.base'] = sklearn.neighbors._base
# !pip install impyute
# !pip install fancyimpute
from sklearn import datasets
from sklearn.preprocessing import LabelEncoder, StandardScaler, MinMaxScaler
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as skLDA
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from scipy import stats
import numpy as np
# import impyute as impy
from fancyimpute import SoftImpute#, MatrixFactorization
import pandas as pd
import time
import math
# from missingpy import MissForest
from sklearn.model_selection import train_test_split
from numpy.linalg import norm, inv

from sklearn.datasets import make_regression
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from fancyimpute import SimpleFill, SoftImpute
from sklearn.pipeline import make_pipeline
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression

import warnings
warnings.filterwarnings("ignore")

In [2]:
data = pd.read_table('https://archive.ics.uci.edu/ml/machine-learning-databases/00236/seeds_dataset.txt',
                     sep = '\s+', header = None)
data = pd.DataFrame.to_numpy(data)
X,y = data[:,:7], data[:,7]-1 # reset the labels to go start from 0  
X.shape, y.shape

((210, 7), (210,))

In [3]:
X[:,6:].shape

(210, 1)

In [4]:
def one_iter(clf, clf1, clf2):
    X1, X2, y1, y2 = train_test_split(X,y.reshape((-1,1)),test_size=0.2)
    Xtrain1, Xtest1, ytrain1, ytest1 = train_test_split(X1,y1.reshape((-1,1)),test_size=0.5)
    Xtrain2, Xtest2, ytrain2, ytest2 = train_test_split(X2,y2.reshape((-1,1)),test_size=0.5)            
    Xtrain1[:, :ndel1] = np.nan
    Xtest1[:,:ndel1] = np.nan
    Xtrain2[:, ndel2:] = np.nan
    Xtest2[:,ndel2:] = np.nan

    Xtrain = np.vstack((Xtrain1, Xtrain2))
    Xtest = np.vstack((Xtest1, Xtest2))
    ytrain = np.vstack((ytrain1, ytrain2)) 
    ytest = np.vstack((ytest1, ytest2))
    
    Xtrain1 = Xtrain1[:,ndel1:]
    Xtrain2 = Xtrain2[:,:ndel2]
    Xtest1 = Xtest1[:,ndel1:]
    Xtest2 = Xtest2[:,:ndel2]
    scaler = MinMaxScaler()
    scaler.fit(Xtrain1)
    Xtrain1 = scaler.transform(Xtrain1)
    Xtest1 = scaler.transform(Xtest1)
    scaler.fit(Xtrain2)
    Xtrain2 = scaler.transform(Xtrain2)
    Xtest2 = scaler.transform(Xtest2)    
    print('Xtrain2.shape:', Xtrain2.shape, 'Xtest2.shape:', Xtest2.shape)

    scaler.fit(Xtrain)
    Xtrain = scaler.transform(Xtrain)
    Xtest = scaler.transform(Xtest)
    Xtrain = SoftImpute(verbose = False).fit_transform(Xtrain)
    Xtest = SoftImpute(verbose = False).fit_transform(Xtest)
    Xtrain1 = SoftImpute(verbose = False).fit_transform(Xtrain1)
    Xtrain2 = SoftImpute(verbose = False).fit_transform(Xtrain2)
    Xtest1 = SoftImpute(verbose = False).fit_transform(Xtest1)
    Xtest2 = SoftImpute(verbose = False).fit_transform(Xtest2)

    print('Xtrain1.shape:', Xtrain1.shape, 'Xtest1.shape:', Xtest1.shape)
    print('Xtrain2.shape:', Xtrain2.shape, 'Xtest2.shape:', Xtest2.shape)    
    clf.fit(Xtrain, ytrain)
    clf1.fit(Xtrain1, ytrain1)
    clf2.fit(Xtrain2, ytrain2)

    return np.array([np.mean(clf.predict(Xtest[:len(ytest1),:])==ytest1.flatten()), 
                     np.mean(clf.predict(Xtest[len(ytest1):,:])==ytest2.flatten()),
                    clf1.score(Xtest1, ytest1),  clf2.score(Xtest2, ytest2)])    

In [9]:
ndel1, ndel2 = 3,3  

clf = LogisticRegression(random_state=0)
clf1 = LogisticRegression(random_state=0)
clf2 = LogisticRegression(random_state=0)
res = np.array([one_iter(clf, clf1, clf2) for i in range(1000)])

Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel

Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d arr

Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


...

Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel

Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\

Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


In [11]:
np.mean(res, axis = 0), np.var(res, axis = 0)

(array([0.91053571, 0.67480952, 0.91555952, 0.72990476]),
 array([0.00109832, 0.02049832, 0.00098928, 0.01664947]))

In [14]:
ndel1, ndel2 = 3,3 
clf = make_pipeline(StandardScaler(), SVC(gamma='auto'))
clf1 = make_pipeline(StandardScaler(), SVC(gamma='auto'))
clf2 = make_pipeline(StandardScaler(), SVC(gamma='auto'))
res = np.array([one_iter(clf, clf1, clf2) for i in range(1000)])

Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel

Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d arr

Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


...

C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not 

Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not 

Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)
Xtrain1.shape: (84, 4) Xtest1.shape: (84, 4)
Xtrain2.shape: (21, 3) Xtest2.shape: (21, 3)


C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\fancyimpute\solver.py:55: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\thung\anaconda3\envs\mtime\lib\site-packages\sklearn\utils\validation.py:1111: DataConversionWarning: A column-vector y was passed when a 1d arr

In [15]:
np.mean(res, axis = 0), np.var(res, axis = 0)

(array([0.92288095, 0.8262381 , 0.92565476, 0.82680952]),
 array([0.00060339, 0.00952335, 0.00058319, 0.00846538]))